# Visualizations of the EEG data in the TF domain

This notebook is used for different basic visualisations in the TF domain

Author: Magnus Evensen, Malte Færgemann Lau $\\$
Project: Bachelor's Project - EEG Social Interaction

In [127]:
import h5py
import numpy as np
import mne
import os
import pandas as pd
import glob
import gc
from tqdm import tqdm

import matplotlib.pyplot as plt
import matplotlib as mpl

# mpl setup
mpl.rcParams['image.cmap'] = 'ocean'
plt.rcParams['axes.prop_cycle'] = plt.cycler(color=plt.cm.ocean(np.linspace(0, 1, 64)))
mpl.rcParams['font.family'] = 'Helvetica Neue'
mpl.rcParams['figure.figsize'] = (6, 4)
mpl.rcParams['lines.linewidth'] = 1
mpl.rcParams['figure.dpi'] = 400
%config InlineBackend.figure_format = 'retina'
%matplotlib inline
dtu_colors = {'dtured' : (0.6,0,0), 'blue': (0.1843,0.2431,0.9176), 'brightgreen' : (0.1216,0.8157,0.5098), 'navyblue' : (0.0118,0.0588,0.3098), 'yellow' : (0.9647,0.8157,0.3019), 'orange' : (0.9882,0.4627,0.2039), 'pink' : (0.9686,0.7333,0.6941), 'grey' : (0.8549,0.8549,0.8549), 'red' : (0.9098,0.2471,0.2824), 'green' : (0,0.5333,0.2078), 'purple' : (0.4745,0.1373,0.5569)}

In [3]:
path = os.path.abspath('./FG_Data/FG_overview_df_v2.pkl')
overview = pd.read_pickle(path)
overview

Subject_id Exp_id Friend_status  EEG_device  Force_device  Force_port  \
0         1049   301A           Yes           1             1           1   
1         1029   301B            No           2             3           2   
2         1028   301C           Yes           3             4           3   
3         1064   302A           Yes           1             1           1   
4         1024   302B           Yes           2             3           2   
..         ...    ...           ...         ...           ...         ...   
87        6069   330B            No           2             3           2   
88        6048   330C           Yes           3             4           3   
89        6015   331A           Yes           1             1           1   
90        6183   331B           Yes           2             3           2   
91        6141   331C            No           3             4           3   

          Age Gender  Class_friends  Class_close_friends  Friends  \
0   22.239562      F              3                    6        9   
1   24.331280      M              3                    1        8   
2   21.670089      M              8                    4        9   
3   22.009582      M             14                    8       11   
4   21.355236      M              5                    7        6   
..        ...    ...            ...                  ...      ...   
87  19.373032      F             14                    3       17   
88  19.841205      M             13                   11       25   
89  20.052019      M              9                    4       14   
90  18.863792      M             22                    6       25   
91  19.633128      M              9                    3       17   

    Close_friends  Triad_id Participant  tFriends  tClose_friends  \
0              14       301          P1        12              20   
1               5       301          P2        11               6   
2               4       301          P3        17               8   
3               5       302          P1        25              13   
4              10       302          P2        11              17   
..            ...       ...         ...       ...             ...   
87             17       330          P2        31              20   
88             26       330          P3        38              37   
89             13       331          P1        23              17   
90             12       331          P2        47              18   
91             10       331          P3        26              13   

    All_friends  tClass    rClass  
0            32       9  0.666667  
1            17       4  0.250000  
2            25      12  0.333333  
3            38      22  0.363636  
4            28      12  0.583333  
..          ...     ...       ...  
87           51      17  0.176471  
88           75      24  0.458333  
89           40      13  0.307692  
90           65      28  0.214286  
91           39      12  0.250000  

[92 rows x 19 columns]

In [4]:
# Define the path
folder_path = os.path.abspath('./FG_Data/PreprocessedEEGData')

# Use glob to find all FIF files in the folder
epoch_files = glob.glob(os.path.join(folder_path, '*-epo.fif'))

# Load each FIF file into a list of epoch objects
epochs_list = [mne.read_epochs(f, preload=False, verbose=False) for f in epoch_files]
sfreq = int(epochs_list[0].info['sfreq'])
n_epochs, n_channels, n_timepoints = epochs_list[0].get_data().shape
len(epochs_list)

Loading data for 298 events and 3000 original time points ...


92

In [11]:
def roof(x):
    return int(x) + 1 if x > int(x) else int(x)

In [161]:
def get_psds_for_channel_for_all_participants(participants_data, channel, settings, window, freq_band = 'Unfiltered'):
    
    overlap = window / 2
    psd_dict = {}
    for setting in settings:
        all_psds = []
        for i, epochs in enumerate(tqdm(participants_data, desc=f'For condition: {setting}, for channel: {channel} with freq band: {freq_band}')):
            # Pick channel 
            filtered_epochs = epochs.load_data().pick([channel])
            band = [4,8] if freq_band=='Theta' else [8,12] if freq_band=='Alpha' else [12,35] if freq_band=='Theta' else False
            if band: # filter epochs to a certain frequency band
                filtered_epochs = filtered_epochs.filter(l_freq=band[0], h_freq=band[1], fir_design='firwin', n_jobs=10, verbose = False) 
            filtered_epochs = filtered_epochs[setting]
            
            powers = []
            for j in range(0,int(6/overlap-1)): # get segments and compute psd using welch transform 
                t0 = j*overlap - 0.5
                t = window + t0 - 1/sfreq
                segment = filtered_epochs.copy().crop(tmin = t0, tmax = t) # Get time segment from samples
                psds = segment.compute_psd(method='welch', fmin=1, fmax=40, n_fft=int(sfreq*window), n_overlap=int(sfreq*0.5*window), n_jobs=10, verbose = False); # what to do about frequency here?
                mean_psds = psds.average()
                powers.append(mean_psds.get_data().mean(axis=1))
            
            powers = np.array(powers)
            baseline = powers[5:11,:].mean() # get baseline psd
            powers = powers/baseline # divide with baseline psd
            all_psds.append(powers)
            
            # Unload data from iteration to save memory space
            del filtered_epochs
            gc.collect()
            
        label = f'{setting}, {freq_band} frequencies, channel {channel}'
        psd_dict[label] = np.reshape(all_psds, (len(all_psds), len(all_psds[0]))) 
        
    return psd_dict

In [153]:
def plot_TF(dict, mean = False): 
    """ Takes a dict where each value should be of size (n_segments, n_channels), \\
    and returns frequency over time plots in a (n_items, 2) grid"""
    times = np.arange(-0.5, 5.5, 6/len(next(iter(dict.values()))[0])) # Create time points equal to powers
    fig, axes = plt.subplots(roof(len(dict)/2), 2, figsize=(12, len(dict)*2), constrained_layout = True)
    axes = axes.flatten()
    for i, (data_label, powers) in enumerate(dict.items()):
        ax = axes[i]
        if mean: # Plot mean with std
            mean_line = np.mean(powers, axis = 0)
            std_line = np.std(powers, axis = 0)
            ax.plot(times, mean_line, label = 'Mean power of channels', color = dtu_colors['navyblue'])
            ax.fill_between(times, mean_line - std_line, mean_line + std_line, color=dtu_colors['navyblue'], alpha=0.3, label='± 1 Std Dev')
        
        else: # Plot each participant
            for power in powers:
                ax.plot(times, power, alpha = 0.5)
            
        ax.axhline(y=1, color='black', linestyle='--', label='baseline', alpha = 0.3) # plot baseline
        ax.set_title(f"{data_label}")
        ax.set_ylim(0,2)
        ax.set_xlim(0,4)
        ax.set_xlabel('Time (s)')
        ax.set_ylabel('Power')
    plt.show()

In [162]:
window = 0.1 # What should window size be?
settings = ['T1P', 'T1Pn', 'T3P', 'T3Pn']
channel = 'C3'
Alpha_psds = get_psds_for_channel_for_all_participants(participants_data=epochs_list, channel=channel, settings=settings, freq_band = "Alpha", window=window)
Beta_psds = get_psds_for_channel_for_all_participants(participants_data=epochs_list, channel=channel, settings=settings, freq_band = "Beta", window=window)
Theta_psds = get_psds_for_channel_for_all_participants(participants_data=epochs_list, channel=channel, settings=settings, freq_band = "Theta", window=window)
unfiltered_psds = get_psds_for_channel_for_all_participants(participants_data=epochs_list, channel=channel, settings=settings, freq_band = 'Unfiltered', window=window)

For condition: T1P, for channel: C3 with freq band: Alpha: 100%|██████████| 92/92 [03:50<00:00,  2.50s/it]
For condition: T1Pn, for channel: C3 with freq band: Alpha: 100%|██████████| 92/92 [04:01<00:00,  2.62s/it]
For condition: T3P, for channel: C3 with freq band: Alpha: 100%|██████████| 92/92 [04:08<00:00,  2.70s/it]
For condition: T3Pn, for channel: C3 with freq band: Alpha: 100%|██████████| 92/92 [04:09<00:00,  2.71s/it]
For condition: T1P, for channel: C3 with freq band: Beta: 100%|██████████| 92/92 [04:02<00:00,  2.64s/it]
For condition: T1Pn, for channel: C3 with freq band: Beta: 100%|██████████| 92/92 [03:51<00:00,  2.52s/it]
For condition: T3P, for channel: C3 with freq band: Beta: 100%|██████████| 92/92 [03:54<00:00,  2.55s/it]
For condition: T3Pn, for channel: C3 with freq band: Beta: 100%|██████████| 92/92 [03:56<00:00,  2.57s/it]
For condition: T1P, for channel: C3 with freq band: Theta: 100%|██████████| 92/92 [04:06<00:00,  2.68s/it]
For condition: T1Pn, for channel: C3 

In [170]:
plot_TF(Alpha_psds, mean = True)

In [164]:
plot_TF(Beta_psds, mean = True)

In [168]:
plot_TF(Theta_psds, mean = True)

In [166]:
plot_TF(unfiltered_psds, mean = True)